In [11]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
from tqdm import tqdm
import random
import seaborn as sns
import matplotlib.pyplot as plt
from geopy.geocoders import Nominatim
import warnings
warnings.filterwarnings('ignore')

import os
import plotly.express as px

import xgboost as xg
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error as MSE

In [10]:
!pip install xgboost

Defaulting to user installation because normal site-packages is not writeable


In [5]:
! pip install geonamescache
! pip install geopandas
! pip install Shapely

Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable


  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.


Defaulting to user installation because normal site-packages is not writeable


In [13]:
mydict= {'ID': list(),
 'Delivery_person_ID': list(),
 'Delivery_person_Age': list(),
 'Delivery_person_Ratings': list(),
 'Restaurant_latitude': list(),
 'Restaurant_longitude': list(),
 'Delivery_location_latitude': list(),
 'Delivery_location_longitude': list(),
 'Order_Date': list(),
 'Time_Orderd': list(),
 'Time_Order_picked': list(),
 'Weather': list(),
 'Road_traffic_density': list(),
 'Vehicle_condition': list(),
 'Type_of_order': list(),
 'Type_of_vehicle': list(),
 'multiple_deliveries': list(),
 'Festival': list(),
 'City': list(),
 'Time_taken': list(),
 'Name:': list()}

In [14]:
mydict_1= {'ID': list(),
 'Delivery_person_ID': list(),
 'Delivery_person_Age': list(),
 'Delivery_person_Ratings': list(),
 'Restaurant_latitude': list(),
 'Restaurant_longitude': list(),
 'Delivery_location_latitude': list(),
 'Delivery_location_longitude': list(),
 'Order_Date': list(),
 'Time_Orderd': list(),
 'Time_Order_picked': list(),
 'Weather': list(),
 'Road_traffic_density': list(),
 'Vehicle_condition': list(),
 'Type_of_order': list(),
 'Type_of_vehicle': list(),
 'multiple_deliveries': list(),
 'Festival': list(),
 'City': list(),
 'Name:': list()}

In [3]:
def get_train_data(path):
    for dirname, _, filenames in os.walk(path):
        for filename in filenames:
            with open(os.path.join(dirname, filename),"r") as file:
                f=file.readlines()
                for i in range(len(f)):
                    k=list(f[i].split())
                    if k[0]== "Time_taken":
                        mydict[k[0]].append(k[2])
                    else:
                        mydict[k[0]].append(k[1])
    data = pd.DataFrame(mydict)
    data = data.drop(["Name:"],axis=1)
    return data

In [15]:
def get_test_data(path):
    for dirname, _, filenames in os.walk(path):
        for filename in filenames:
            with open(os.path.join(dirname, filename),"r") as file:
                f=file.readlines()
                for i in range(len(f)):
                    k=list(f[i].split())
                    if k[0]== "Time_taken":
                        mydict_1[k[0]].append(k[2])
                    else:
                        mydict_1[k[0]].append(k[1])
    data = pd.DataFrame(mydict_1)
    data = data.drop(["Name:"],axis=1)
    return data

In [16]:
train = get_train_data('train')

In [17]:
train

ID Delivery_person_ID Delivery_person_Age Delivery_person_Ratings  \
0      0x4607     INDORES13DEL02           37.000000                4.900000   
1      0xb379     BANGRES18DEL02           34.000000                4.500000   
2      0x5d6d     BANGRES19DEL01           23.000000                4.400000   
3      0x7a6a    COIMBRES13DEL02           38.000000                4.700000   
4      0x70a2     CHENRES12DEL01           32.000000                4.600000   
...       ...                ...                 ...                     ...   
45588  0x7c09      JAPRES04DEL01           30.000000                4.800000   
45589  0xd641      AGRRES16DEL01               21.00                    4.60   
45590  0x4f8d     CHENRES08DEL03           30.000000                4.900000   
45591  0x5eee    COIMBRES11DEL01           20.000000                4.700000   
45592  0x5fb2   RANCHIRES09DEL02           23.000000                4.900000   

      Restaurant_latitude Restaurant_longitude Delivery_location_latitude  \
0               22.745049            75.892471                  22.765049   
1               12.913041            77.683237                  13.043041   
2               12.914264            77.678400                  12.924264   
3               11.003669            76.976494                  11.053669   
4               12.972793            80.249982                  13.012793   
...                   ...                  ...                        ...   
45588           26.902328            75.794257                  26.912328   
45589                0.00                 0.00                       0.07   
45590           13.022394            80.242439                  13.052394   
45591           11.001753            76.986241                  11.041753   
45592           23.351058            85.325731                  23.431058   

      Delivery_location_longitude  Order_Date Time_Orderd Time_Order_picked  \
0                       75.912471  19-03-2022       11:30             11:45   
1                       77.813237  25-03-2022       19:45             19:50   
2                       77.688400  19-03-2022        8:30              8:45   
3                       77.026494  05-04-2022       17:60             18:10   
4                       80.289982  26-03-2022       13:30             13:45   
...                           ...         ...         ...               ...   
45588                   75.804257  24-03-2022       11:35             11:45   
45589                        0.07  16-02-2022       19:55             20:10   
45590                   80.272439  11-03-2022       23:50             24:05   
45591                   77.026241  07-03-2022       13:35             13:40   
45592                   85.405731  02-03-2022       17:10             17:15   

          Weather Road_traffic_density Vehicle_condition Type_of_order  \
0      conditions                 High                 2         Snack   
1      conditions                  Jam                 2         Snack   
2      conditions                  Low                 0        Drinks   
3      conditions               Medium                 0        Buffet   
4      conditions                 High                 1         Snack   
...           ...                  ...               ...           ...   
45588  conditions                 High                 1          Meal   
45589  conditions                  Jam                 0        Buffet   
45590  conditions                  Low                 1        Drinks   
45591  conditions                 High                 0         Snack   
45592  conditions               Medium                 2         Snack   

      Type_of_vehicle multiple_deliveries Festival           City Time_taken  
0          motorcycle            0.000000       No          Urban  24.000000  
1             scooter            1.000000       No  Metropolitian  33.000000  
2          motorcycle            1.000000       No

In [18]:
test = get_test_data('test')

In [19]:
test

ID Delivery_person_ID Delivery_person_Age Delivery_person_Ratings  \
0      0x2318    COIMBRES13DEL01                 NaN                     NaN   
1      0x3474     BANGRES15DEL01           28.000000                4.600000   
2      0x9420      JAPRES09DEL03           23.000000                4.500000   
3      0x72ee      JAPRES07DEL03           21.000000                4.800000   
4      0xa759     CHENRES19DEL01           31.000000                4.600000   
...       ...                ...                 ...                     ...   
11394  0x6909      JAPRES01DEL01           35.000000                4.600000   
11395  0x443b      JAPRES11DEL01           33.000000                4.900000   
11396  0x1ea5      SURRES11DEL03                 NaN                     NaN   
11397  0x22d4      VADRES03DEL02               27.00                    4.70   
11398  0xb7be     CHENRES07DEL02           39.000000                5.000000   

      Restaurant_latitude Restaurant_longitude Delivery_location_latitude  \
0               11.003669            76.976494                  11.043669   
1               12.975377            77.696664                  13.085377   
2               26.911378            75.789034                  27.001378   
3               26.766536            75.837333                  26.856536   
4               12.986047            80.218114                  13.096047   
...                   ...                  ...                        ...   
11394           26.905190            75.810753                  27.015190   
11395           26.902940            75.793007                  26.912940   
11396           21.157735            72.768778                  21.217735   
11397               22.32                73.17                      22.45   
11398           13.081878            80.248519                  13.131878   

      Delivery_location_longitude  Order_Date Time_Orderd Time_Order_picked  \
0                       77.016494  30-03-2022         NaN             15:05   
1                       77.806664  29-03-2022       20:30             20:35   
2                       75.879034  10-03-2022       19:35             19:45   
3                       75.927333  02-04-2022       17:15             17:20   
4                       80.328114  27-03-2022       18:25             18:40   
...                           ...         ...         ...               ...   
11394                   75.920753  27-03-2022       21:35             21:45   
11395                   75.803007  11-03-2022       11:40             11:45   
11396                   72.828778  11-03-2022         NaN             21:05   
11397                       73.30  06-03-2022       18:35             18:40   
11398                   80.298519  24-03-2022       22:20             22:25   

          Weather Road_traffic_density Vehicle_condition Type_of_order  \
0      conditions                  NaN                 3        Drinks   
1      conditions                  Jam                 0         Snack   
2      conditions                  Jam                 0        Drinks   
3      conditions               Medium                 1          Meal   
4      conditions               Medium                 2        Drinks   
...           ...                  ...               ...           ...   
11394  conditions                  Jam                 1         Snack   
11395  conditions                 High                 1        Drinks   
11396  conditions                  NaN                 3        Drinks   
11397  conditions               Medium                 0          Meal   
11398  conditions                  Low                 2        Drinks   

        Type_of_vehicle multiple_deliveries Festival           City  
0      electric_scooter            1.000000       No  Metropolitian  
1            motorcycle            1.000000       No  Metropolitian  
2            motorcycle            1.000000       No  Metropolitian  
3      

In [20]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45593 entries, 0 to 45592
Data columns (total 20 columns):
 #   Column                       Non-Null Count  Dtype 
---  ------                       --------------  ----- 
 0   ID                           45593 non-null  object
 1   Delivery_person_ID           45593 non-null  object
 2   Delivery_person_Age          45593 non-null  object
 3   Delivery_person_Ratings      45593 non-null  object
 4   Restaurant_latitude          45593 non-null  object
 5   Restaurant_longitude         45593 non-null  object
 6   Delivery_location_latitude   45593 non-null  object
 7   Delivery_location_longitude  45593 non-null  object
 8   Order_Date                   45593 non-null  object
 9   Time_Orderd                  45593 non-null  object
 10  Time_Order_picked            45593 non-null  object
 11  Weather                      45593 non-null  object
 12  Road_traffic_density         45593 non-null  object
 13  Vehicle_condition            45

In [21]:
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11399 entries, 0 to 11398
Data columns (total 19 columns):
 #   Column                       Non-Null Count  Dtype 
---  ------                       --------------  ----- 
 0   ID                           11399 non-null  object
 1   Delivery_person_ID           11399 non-null  object
 2   Delivery_person_Age          11399 non-null  object
 3   Delivery_person_Ratings      11399 non-null  object
 4   Restaurant_latitude          11399 non-null  object
 5   Restaurant_longitude         11399 non-null  object
 6   Delivery_location_latitude   11399 non-null  object
 7   Delivery_location_longitude  11399 non-null  object
 8   Order_Date                   11399 non-null  object
 9   Time_Orderd                  11399 non-null  object
 10  Time_Order_picked            11399 non-null  object
 11  Weather                      11399 non-null  object
 12  Road_traffic_density         11399 non-null  object
 13  Vehicle_condition            11

In [22]:
print(train.shape)
print(test.shape)

(45593, 20)
(11399, 19)


In [23]:
fig = px.scatter_geo(train,lat='Restaurant_latitude',lon='Restaurant_longitude', hover_name="ID")
fig.update_layout(title = 'Restaurant_location_train_data', title_x=0.5)
fig.show()

In [24]:
fig = px.scatter_geo(test,lat='Restaurant_latitude',lon='Restaurant_longitude', hover_name="ID")
fig.update_layout(title = 'Restaurant_location_train_data', title_x=0.5)
fig.show()

In [25]:
def get_NaN(data):
    for i in data.columns:
        counter=0
        for j in range(data.shape[0]):
            if data[i].iloc[j]=="NaN":
                counter+=1
            else:
                pass
        print(i,counter)
get_NaN(train)

ID 0
Delivery_person_ID 0
Delivery_person_Age 1854
Delivery_person_Ratings 1908
Restaurant_latitude 0
Restaurant_longitude 0
Delivery_location_latitude 0
Delivery_location_longitude 0
Order_Date 0
Time_Orderd 1731
Time_Order_picked 0
Weather 0
Road_traffic_density 601
Vehicle_condition 0
Type_of_order 0
Type_of_vehicle 0
multiple_deliveries 993
Festival 228
City 1200
Time_taken 0


In [27]:
get_NaN(test)

ID 0
Delivery_person_ID 0
Delivery_person_Age 491
Delivery_person_Ratings 507
Restaurant_latitude 0
Restaurant_longitude 0
Delivery_location_latitude 0
Delivery_location_longitude 0
Order_Date 0
Time_Orderd 444
Time_Order_picked 0
Weather 0
Road_traffic_density 154
Vehicle_condition 0
Type_of_order 0
Type_of_vehicle 0
multiple_deliveries 238
Festival 65
City 324


Lets try to solve for festival using order date.
The idea is to stack all the order dates which have Festival as true and try to fill in NaN values with help of those dates

In [28]:
def check(data):
    month,year=[],[]
    for i in range(data.shape[0]):
        d=data["Order_Date"].iloc[i].split("-")
        month.append(d[1])
        year.append(d[2])
    print("Months",set(month))
    print("Year", set(year))
print("Train : ")
check(train)
print("Test : ")
check(test)

Train : 
Months {'04', '02', '03'}
Year {'2022'}
Test : 
Months {'04', '02', '03'}
Year {'2022'}


In [29]:
train["Festival"].value_counts()

No     44469
Yes      896
NaN      228
Name: Festival, dtype: int64

In [30]:
test["Festival"].value_counts()

No     11131
Yes      203
NaN       65
Name: Festival, dtype: int64

In [31]:
l=list(train[train.Festival=="Yes"].Order_Date)
l.extend(list(test[test.Festival=="Yes"].Order_Date))
holidays=list(set(l))
print("all the Festivals date")
holidays

all the Festivals date


['14-02-2022',
 '01-03-2022',
 '21-03-2022',
 '11-03-2022',
 '08-03-2022',
 '17-03-2022',
 '04-03-2022',
 '05-03-2022',
 '06-04-2022',
 '18-02-2022',
 '05-04-2022',
 '07-03-2022',
 '20-03-2022',
 '11-02-2022',
 '30-03-2022',
 '27-03-2022',
 '24-03-2022',
 '02-04-2022',
 '14-03-2022',
 '03-03-2022',
 '15-03-2022',
 '23-03-2022',
 '16-03-2022',
 '13-03-2022',
 '17-02-2022',
 '13-02-2022',
 '09-03-2022',
 '10-03-2022',
 '12-03-2022',
 '01-04-2022',
 '12-02-2022',
 '18-03-2022',
 '28-03-2022',
 '19-03-2022',
 '04-04-2022',
 '31-03-2022',
 '15-02-2022',
 '26-03-2022',
 '25-03-2022',
 '29-03-2022',
 '02-03-2022',
 '03-04-2022',
 '06-03-2022',
 '16-02-2022']

In [32]:
def fill_NaN_festival(data):
    for i in range(data.shape[0]):
        if data["Festival"].iloc[i]=="NaN":
            if data["Order_Date"].iloc[i] in holidays:
                data["Festival"].iloc[i]="Yes"
            else:
                data["Festival"].iloc[i]="No"
        else:
            pass
    data["Festival"]=data["Festival"].astype('category')
fill_NaN_festival(train)
fill_NaN_festival(test)

In [33]:
train["Festival"].value_counts()

No     44469
Yes     1124
Name: Festival, dtype: int64

In [34]:
test["Festival"].value_counts()

No     11131
Yes      268
Name: Festival, dtype: int64

In [35]:
def clean_multiple_deliveries(data):
    for i in tqdm(range(data.shape[0])):
        if data.multiple_deliveries.iloc[i] != "NaN":
            data.multiple_deliveries.iloc[i] = int(str(data.multiple_deliveries.iloc[i])[0])
            pass
        else:
            # replace NaN with 1
            data.multiple_deliveries.iloc[i] = 1
    data["multiple_deliveries"]=data["multiple_deliveries"].astype('int64')
clean_multiple_deliveries(train)
clean_multiple_deliveries(test)

100%|██████████| 11399/11399 [08:38<00:00, 21.98it/s]


In [36]:
def clean_delivey_person_age(data):
    for i in tqdm(range(data.shape[0])):
        if data.Delivery_person_Age.iloc[i] != "NaN":
            data.Delivery_person_Age.iloc[i] = int(str(data.Delivery_person_Age.iloc[i])[:2])
        else:
            # replace NaN with median
            data.Delivery_person_Age.iloc[i] = data.Delivery_person_Age.median()
            # replace NaN with mode
            #data.Delivery_person_Age.iloc[i] = data.Delivery_person_Age.mode()
#train["Delivery_person_Age"]=pd.to_numeric(train["Delivery_person_Age"], downcast='float')
clean_delivey_person_age(train)
clean_delivey_person_age(test)
train["Delivery_person_Age"]=train["Delivery_person_Age"].astype('int64')
test["Delivery_person_Age"]=test["Delivery_person_Age"].astype('int64')

100%|██████████| 11399/11399 [08:44<00:00, 21.74it/s] 


In [37]:
def clean_Delivery_person_Ratings(data):
    mod = data.Delivery_person_Ratings.mode()
    for i in tqdm(range(data.shape[0])):
        #print(i)
        if data.Delivery_person_Ratings.iloc[i] != "NaN":
            data.Delivery_person_Ratings.iloc[i] = float(str(data.Delivery_person_Ratings.iloc[i])[:3])
        else:
            # replace NaN with median
            data.Delivery_person_Ratings.iloc[i] = data.Delivery_person_Ratings.median()
            
            #replace NaN with mode
            # data.Delivery_person_Ratings.iloc[i] = data.Delivery_person_Ratings.mode()
    data["Delivery_person_Ratings"]=pd.to_numeric(data["Delivery_person_Ratings"], downcast='float')
            
clean_Delivery_person_Ratings(train)
clean_Delivery_person_Ratings(test)

100%|██████████| 11399/11399 [08:18<00:00, 22.89it/s]


In [38]:
train[(train.City=="NaN") & (train.Road_traffic_density=="NaN")]

ID Delivery_person_ID  Delivery_person_Age  \
2233    0x529    COIMBRES09DEL03                   30   
4950    0x44b     BANGRES18DEL02                   30   
5217    0x4f6    COIMBRES14DEL01                   30   
6319    0x861      MYSRES03DEL02                   30   
7762    0x5e2      MYSRES05DEL02                   30   
10027   0x4ce     BANGRES20DEL01                   30   
10464   0x50b      MUMRES03DEL01                   30   
15372   0x590   RANCHIRES05DEL03                   30   
19955  0xbf08     LUDHRES17DEL01                   30   
21062   0x5e7   RANCHIRES16DEL02                   30   
21437  0x1380      MYSRES19DEL02                   30   
22921  0x1067      VADRES03DEL03                   30   
26652   0x6e5     INDORES11DEL02                   30   
27221   0x3f4    COIMBRES20DEL02                   50   
28754   0x742     INDORES06DEL01                   30   
32326  0xbf33      KNPRES03DEL03                   50   
34070   0x496     CHENRES07DEL01                   30   
35929   0x605      MYSRES20DEL02                   30   
37390   0xd44      HYDRES17DEL01                   30   
43407   0x409      JAPRES18DEL03                   30   
45504   0x461     BANGRES07DEL02                   30   

       Delivery_person_Ratings Restaurant_latitude Restaurant_longitude  \
2233                       4.7           11.008638            76.984311   
4950                       4.7           12.913041            77.683237   
5217                       4.7          -11.003681           -76.975525   
6319                       4.7           12.299524            76.642620   
7762                       4.7          -12.323978            76.627961   
10027                      4.7          -12.972161           -77.596014   
10464                      4.7          -19.223840           -72.841347   
15372                      4.7          -23.355164            85.324097   
19955                      4.7          -30.893384           -75.821202   
21062                      4.7          -23.371292            85.327872   
21437                      4.7           12.334022            76.618203   
22921                      4.7               22.32                73.17   
26652                      4.7           22.751234            75.889490   
27221                      6.0          -10.994136           -76.963303   
28754                      4.7           22.728163            75.884212   
32326                      6.0          -26.469003           -80.316344   
34070                      4.7          -13.081878           -80.248519   
35929                      4.7           12.337978            76.616792   
37390                      4.7           17.451976            78.385883   
43407                      4.7           26.913987            75.752891   
45504                      4.7          -12.978453           -77.643685   

      Delivery_location_latitude Delivery_location_longitude  Order_Date  \
2233                   11.038638                   77.014311  05-04-2022   
4950                   13.043041                   77.813237  31-03-2022   
5217                   11.073681                   77.045525  02-04-2022   
6319                   12.429524                   76.772620  08-03-2022   
7762                   12.343978                   76.647961  01-03-2022   
10027                  13.082161                   77.706014  12-03-2022   
10464                  19.263840                   72.881347  05-03-2022   
15372                  23.385164                   85.354097  05-04-2022   
19955                  30.903384                   75.831202  11-02-2022   
21062                  23.391292                   85.347872  03-03-2022   
21437                  12.354022                   76.638203  26-03-2022   
22921                      22.41                       73.26  25-03-2022   
26652                  22.771234                   75.909490  21-03-2022   
27221                  11.074136         

In [39]:
temp={ "Metropolitian" : ['Jam', 'Low', 'Medium'] ,
        "Urban" : ['Low' , 'Jam' , 'Medium'] ,
      "Semi-Urban" : ["Jam"]
}

def clean_Road_traffic_density(data):
    for i in tqdm(range(data.shape[0])):
        if data.Road_traffic_density.iloc[i] == 'NaN':
            if data.City.iloc[i] == 'Metropolitian':
                data.Road_traffic_density.iloc[i] = random.choice(temp['Metropolitian'])
            elif data.City.iloc[i] == 'Urban':
                data.Road_traffic_density.iloc[i] = random.choice(temp['Urban'])
            elif data.City.iloc[i] == 'Semi-Urban':
                data.Road_traffic_density.iloc[i] = random.choice(temp['Semi-Urban'])
            else:
                data.Road_traffic_density.iloc[i] = random.choice(temp['Metropolitian'])
        else:
            pass
    data["Road_traffic_density"]=data["Road_traffic_density"].astype('category')
clean_Road_traffic_density(train)
clean_Road_traffic_density(test)

100%|██████████| 11399/11399 [00:08<00:00, 1324.88it/s]


In [40]:
# storing to create the final csv
t= test["ID"]

In [41]:
train = train.drop(["City", "Time_Orderd", "ID", "Delivery_person_ID"],axis=1)
test = test.drop(["City", "Time_Orderd", "ID", "Delivery_person_ID" ],axis=1)

In [42]:
def lat_long(data):
    data["Restaurant_longitude"]=pd.to_numeric(data["Restaurant_longitude"], downcast='float')
    data["Delivery_location_latitude"]=pd.to_numeric(data["Delivery_location_latitude"], downcast='float')
    data["Delivery_location_longitude"]=pd.to_numeric(data["Delivery_location_longitude"], downcast='float')
    data["Restaurant_latitude"]=pd.to_numeric(data["Restaurant_latitude"], downcast='float')
lat_long(train)
lat_long(test)

In [43]:
train=train.drop(['Order_Date'],axis=1)
test=test.drop(['Order_Date'],axis=1)

In [44]:
def config_Time_Order_picked(data):
    for i in tqdm(range(data.shape[0])):
        data.Time_Order_picked.iloc[i] = float(str(data.Time_Order_picked.iloc[i]).replace(":","."))
    data["Time_Order_picked"]=pd.to_numeric(data["Time_Order_picked"], downcast='float')
config_Time_Order_picked(train)
config_Time_Order_picked(test)

100%|██████████| 11399/11399 [06:52<00:00, 27.60it/s]


In [47]:
def prepocess_Time_taken(data):
    data["Time_taken"]=pd.to_numeric(data["Time_taken"], downcast='integer')
prepocess_Time_taken(train)

In [48]:
def change_types(data):
    data["Weather"]=data["Weather"].astype('category')
    data["Vehicle_condition"]=data["Vehicle_condition"].astype('int64')
    data["Type_of_order"]=data["Type_of_order"].astype('category')
    data["Type_of_vehicle"]=data["Type_of_vehicle"].astype('category')
change_types(train)
change_types(test)

In [49]:
train=pd.get_dummies(train)
test=pd.get_dummies(test)

In [50]:
print(train.shape)
print(test.shape)

(45593, 25)
(11399, 24)


In [51]:
X,y = train.drop(["Time_taken"],axis=1),train["Time_taken"]

In [52]:
# Splitting
train_X, test_X, train_y, test_y = train_test_split(X, y,test_size = 0.3, random_state = 123)

In [53]:
xgb_r = xg.XGBRegressor(n_estimators=700, max_depth=6, learning_rate = 0.01)

  
# Fitting the model
xgb_r.fit(train_X, train_y)
  
# Predict the model
pred = xgb_r.predict(test_X)
  
# RMSE Computation
rmse = np.sqrt(MSE(test_y, pred))
print("RMSE : % f" %(rmse))

RMSE :  5.719566


In [54]:
result= {"ID":t, "Time_taken (min)":list(xgb_r.predict(test))}
res = pd.DataFrame(result)
res["Time_taken (min)"]=pd.to_numeric(res["Time_taken (min)"], downcast='float')
for i in tqdm(range(res.shape[0])):
    res["Time_taken (min)"].iloc[i]= round(float(round(res["Time_taken (min)"].iloc[i])),1)

100%|██████████| 11399/11399 [06:29<00:00, 29.29it/s]


In [74]:
res

ID  Time_taken (min)
0      0x2318              27.0
1      0x3474              30.0
2      0x9420              31.0
3      0x72ee              23.0
4      0xa759              26.0
...       ...               ...
11394  0x6909              30.0
11395  0x443b              28.0
11396  0x1ea5              27.0
11397  0x22d4              24.0
11398  0xb7be              22.0

[11399 rows x 2 columns]

In [56]:
# save as csv
res.to_csv("result1.csv", index=False)